In [1]:
# Install the required packages
%pip install torch torchaudio

import torch
import torchaudio

print(torch.__version__)
print(torchaudio.__version__)

import matplotlib.pyplot as plt


[notice] A new release of pip is available: 24.1.2 -> 24.3.1
[notice] To update, run: pip3 install --upgrade pip
Note: you may need to restart the kernel to use updated packages.
2.5.1
2.5.1


In [2]:
# Install the required package
%pip install mir_eval

from IPython.display import Audio
from mir_eval import separation
from torchaudio.pipelines import HDEMUCS_HIGH_MUSDB_PLUS
from torchaudio.utils import download_asset


[notice] A new release of pip is available: 24.1.2 -> 24.3.1
[notice] To update, run: pip3 install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [3]:
import certifi
import os

os.environ['SSL_CERT_FILE'] = certifi.where()

bundle = HDEMUCS_HIGH_MUSDB_PLUS

model = bundle.get_model()

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

model.to(device)

sample_rate = bundle.sample_rate

print(f"Sample rate: {sample_rate}")

Sample rate: 44100


/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/torchaudio/pipelines/_source_separation_pipeline.py:56: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental fe

In [4]:
from torchaudio.transforms import Fade


def separate_sources(
    model,
    mix,
    segment=10.0,
    overlap=0.1,
    device=None,
):
    """
    Apply model to a given mixture. Use fade, and add segments together in order to add model segment by segment.

    Args:
        segment (int): segment length in seconds
        device (torch.device, str, or None): if provided, device on which to
            execute the computation, otherwise `mix.device` is assumed.
            When `device` is different from `mix.device`, only local computations will
            be on `device`, while the entire tracks will be stored on `mix.device`.
    """
    if device is None:
        device = mix.device
    else:
        device = torch.device(device)

    batch, channels, length = mix.shape

    chunk_len = int(sample_rate * segment * (1 + overlap))
    start = 0
    end = chunk_len
    overlap_frames = overlap * sample_rate
    fade = Fade(fade_in_len=0, fade_out_len=int(overlap_frames), fade_shape="linear")

    final = torch.zeros(batch, len(model.sources), channels, length, device=device)

    while start < length - overlap_frames:
        chunk = mix[:, :, start:end]
        with torch.no_grad():
            out = model.forward(chunk)
        out = fade(out)
        final[:, :, :, start:end] += out
        if start == 0:
            fade.fade_in_len = int(overlap_frames)
            start += int(chunk_len - overlap_frames)
        else:
            start += chunk_len
        end += chunk_len
        if end >= length:
            fade.fade_out_len = 0
    return final


def plot_spectrogram(stft, title="Spectrogram"):
    magnitude = stft.abs()
    spectrogram = 20 * torch.log10(magnitude + 1e-8).numpy()
    _, axis = plt.subplots(1, 1)
    axis.imshow(spectrogram, cmap="viridis", vmin=-60, vmax=0, origin="lower", aspect="auto")
    axis.set_title(title)
    plt.tight_layout()

In [5]:
%pip install pydub
%pip install ffmpeg
%pip install ffprobe
from pydub import AudioSegment
SAMPLE_SONG = "17_twinkle_twinkle_little_star.mp3" 

# Load the MP3 file
audio = AudioSegment.from_mp3(SAMPLE_SONG)

# Export as WAV
wav_file = SAMPLE_SONG.replace(".mp3", ".wav")
audio.export(wav_file, format="wav")

print(f"Converted {SAMPLE_SONG} to {wav_file}")


[notice] A new release of pip is available: 24.1.2 -> 24.3.1
[notice] To update, run: pip3 install --upgrade pip
Note: you may need to restart the kernel to use updated packages.

[notice] A new release of pip is available: 24.1.2 -> 24.3.1
[notice] To update, run: pip3 install --upgrade pip
Note: you may need to restart the kernel to use updated packages.

[notice] A new release of pip is available: 24.1.2 -> 24.3.1
[notice] To update, run: pip3 install --upgrade pip
Note: you may need to restart the kernel to use updated packages.
Converted 17_twinkle_twinkle_little_star.mp3 to 17_twinkle_twinkle_little_star.wav


In [6]:
# Install Python dependencies
%pip install --upgrade torchaudio
%pip install soundfile
%pip install librosa

import os
import torch
import torchaudio
import soundfile as sf

# Check file exists
SAMPLE_SONG = "17_twinkle_twinkle_little_star.wav"
if not os.path.isfile(SAMPLE_SONG):
    raise FileNotFoundError(f"File not found: {SAMPLE_SONG}")

# Try multiple loading approaches
try:
    # Try default loading
    waveform, sample_rate = torchaudio.load(SAMPLE_SONG)
except:
    try:
        # Try soundfile backend
        data, samplerate = sf.read(SAMPLE_SONG)
        waveform = torch.from_numpy(data).T
        sample_rate = samplerate
    except:
        # Final fallback using librosa
        import librosa
        data, sample_rate = librosa.load(SAMPLE_SONG)
        waveform = torch.from_numpy(data).unsqueeze(0)

# Setup device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
waveform = waveform.to(device)
mixture = waveform

# Parameters
segment: int = 10
overlap = 0.1

print(f"Loaded audio with shape {waveform.shape} at {sample_rate}Hz")


[notice] A new release of pip is available: 24.1.2 -> 24.3.1
[notice] To update, run: pip3 install --upgrade pip
Note: you may need to restart the kernel to use updated packages.

[notice] A new release of pip is available: 24.1.2 -> 24.3.1
[notice] To update, run: pip3 install --upgrade pip
Note: you may need to restart the kernel to use updated packages.

[notice] A new release of pip is available: 24.1.2 -> 24.3.1
[notice] To update, run: pip3 install --upgrade pip
Note: you may need to restart the kernel to use updated packages.
Loaded audio with shape torch.Size([2, 6061824]) at 44100Hz


In [8]:
print("Separating track")

ref = waveform.mean(0)
waveform = (waveform - ref.mean()) / ref.std()  # normalization
waveform = waveform.float()  # Convert to float

sources = separate_sources(
    model,
    waveform[None],
    device=device,
    segment=segment,
    overlap=overlap,
)[0]
sources = sources * ref.std() + ref.mean()

sources_list = model.sources
sources = list(sources)

audios = dict(zip(sources_list, sources))

Separating track


In [9]:
N_FFT = 4096
N_HOP = 4
stft = torchaudio.transforms.Spectrogram(
    n_fft=N_FFT,
    hop_length=N_HOP,
    power=None,
)

In [10]:
def output_results(predicted_source: torch.Tensor, source: str):
    #plot_spectrogram(stft(predicted_source)[0], f"Spectrogram - {source}")
    return Audio(predicted_source, rate=sample_rate)


segment_start = 10
segment_end = 20

frame_start = segment_start * sample_rate
frame_end = segment_end * sample_rate

drums_spec = audios["drums"][:, frame_start:frame_end].cpu()

bass_spec = audios["bass"][:, frame_start:frame_end].cpu()

vocals_spec = audios["vocals"][:, frame_start:frame_end].cpu()

other_spec = audios["other"][:, frame_start:frame_end].cpu()

mix_spec = mixture[:, frame_start:frame_end].cpu()

In [11]:
output_results(vocals_spec, "vocals")

In [12]:
output_results(mix_spec, "mix")